In [18]:
# coding: utf-8

# In[ ]:


import requests             
from bs4 import BeautifulSoup 
import csv                  
import webbrowser
import io
import re

def display(content, filename='output.html'):
    with open(filename, 'wb') as f:
        f.write(content)
        webbrowser.open(filename)

def get_soup(session, url, show=False):
    r = session.get(url)
    if show:
        display(r.content, 'temp.html')

    if r.status_code != 200: # not OK
        print('[get_soup] status code:', r.status_code)
    else:
        return BeautifulSoup(r.text, 'html.parser')
    
def post_soup(session, url, params, show=False):
    '''Read HTML from server and convert to Soup'''

    r = session.post(url, data=params)
    
    if show:
        display(r.content, 'temp.html')

    if r.status_code != 200: # not OK
        print('[post_soup] status code:', r.status_code)
    else:
        return BeautifulSoup(r.text, 'html.parser')
    
def scrape(url, lang='ALL'):

    # create session to keep all cookies (etc.) between requests
    session = requests.Session()

    session.headers.update({
        'User-Agent': 'Mozilla/5.0 (X11; Ubuntu; Linux x86_64; rv:57.0) Gecko/20100101 Firefox/57.0',
    })


    items = parse(session, url + '?filterLang=' + lang)

    return items

def parse(session, url):
    '''Get number of reviews and start getting subpages with reviews'''

    print('[parse] url:', url)

    soup = get_soup(session, url)

    if not soup:
        print('[parse] no soup:', url)
        return

    num_reviews = soup.find('span', class_='reviews_header_count').text # get text
    num_reviews = num_reviews[1:-1] 
    num_reviews = num_reviews.replace(',', '')
    num_reviews = int(num_reviews) # convert text into integer
    print('[parse] num_reviews ALL:', num_reviews)

    url_template = url.replace('.html', '-or{}.html')
    print('[parse] url_template:', url_template)

    items = []

    offset = 0

    while(True):
        subpage_url = url_template.format(offset)

        subpage_items = parse_reviews(session, subpage_url)
        if not subpage_items:
            break

        items += subpage_items

        if len(subpage_items) < 5:
            break

        offset += 5

    return items

def get_reviews_ids(soup):

    items = soup.find_all('div', attrs={'data-reviewid': True})

    if items:
        reviews_ids = [x.attrs['data-reviewid'] for x in items][::2]
        print('[get_reviews_ids] data-reviewid:', reviews_ids)
        return reviews_ids
    
def get_more(session, reviews_ids):

    url = 'https://www.tripadvisor.com/OverlayWidgetAjax?Mode=EXPANDED_HOTEL_REVIEWS_RESP&metaReferer=Hotel_Review'

    payload = {
        'reviews': ','.join(reviews_ids), # ie. "577882734,577547902,577300887",
        #'contextChoice': 'DETAIL_HR', # ???
        'widgetChoice': 'EXPANDED_HOTEL_REVIEW_HSX', # ???
        'haveJses': 'earlyRequireDefine,amdearly,global_error,long_lived_global,apg-Hotel_Review,apg-Hotel_Review-in,bootstrap,desktop-rooms-guests-dust-en_US,responsive-calendar-templates-dust-en_US,taevents',
        'haveCsses': 'apg-Hotel_Review-in',
        'Action': 'install',
    }

    soup = post_soup(session, url, payload)

    return soup

def parse_reviews(session, url):
    '''Get all reviews from one page'''

    print('[parse_reviews] url:', url)

    soup =  get_soup(session, url)

    if not soup:
        print('[parse_reviews] no soup:', url)
        return

    hotel_name = soup.find('h1', id='HEADING').text

    reviews_ids = get_reviews_ids(soup)
    if not reviews_ids:
        return

    soup = get_more(session, reviews_ids)

    if not soup:
        print('[parse_reviews] no soup:', url)
        return

    items = []

    for idx, review in enumerate(soup.find_all('div', class_='reviewSelector')):

        badgets = review.find_all('span', class_='badgetext')
        if len(badgets) > 0:
            contributions = badgets[0].text
        else:
            contributions = '0'

        if len(badgets) > 1:
            helpful_vote = badgets[1].text
        else:
            helpful_vote = '0'
        user_loc = review.select_one('div.userLoc strong')
        if user_loc:
            user_loc = user_loc.text
        else:
            user_loc = ''
            
        bubble_rating = review.select_one('span.ui_bubble_rating')['class']
        bubble_rating = bubble_rating[1].split('_')[-1]

        item = {
            'review_body': review.find('p', class_='partial_entry').text,
            'review_date': review.find('span', class_='ratingDate')['title'], # 'ratingDate' instead of 'relativeDate'
            'rating' : review.find('span', class_= "ui_bubble_rating"),
        }

#[y for y in ['ui_bubble_rating bubble_50', "ui_bubble_rating bubble_45", 
                                                               # "ui_bubble_rating bubble_40", "ui_bubble_rating bubble_35",
                                                               # "ui_bubble_rating bubble_30", "ui_bubble_rating bubble_25",
                                                               # "ui_bubble_rating bubble_20", "ui_bubble_rating bubble_15",
                                                                # "ui_bubble_rating bubble_10","ui_bubble_rating bubble_5"]]
        items.append(item)
        print('\n--- review ---\n')
        for key,val in item.items():
            print(' ', key, ':', val)

    print()

    return items

def write_in_csv(items, filename='results.csv',
                  headers=['hotel name', 'review title', 'review body',
                           'review date', 'contributions', 'helpful vote',
                           'user name' , 'user location', 'rating'],
                  mode='w'):

    print('--- CSV ---')

    with io.open(filename, mode, encoding="utf-8") as csvfile:
        csv_file = csv.DictWriter(csvfile, headers)

        if mode == 'w':
            csv_file.writeheader()

        csv_file.writerows(items)
        
DB_COLUMN   = 'review_body'
DB_COLUMN1 = 'review_date'
DB_COLUMN2 = 'rating'

start_urls = [
    'https://www.tripadvisor.com/Hotel_Review-g60713-d80999-Reviews-Grand_Hyatt_San_Francisco-San_Francisco_California.html',
]

lang = 'en'

headers = [ 
    DB_COLUMN, 
    DB_COLUMN1, 
    DB_COLUMN2,
]

for url in start_urls:

    # get all reviews for 'url' and 'lang'
    items = scrape(url, lang)

    if not items:
        print('No reviews')
    else:
        # write in CSV
        filename = url.split('Reviews-')[1][:-5] + '__' + lang
        print('filename:', filename)
        write_in_csv(items, filename + '.csv', headers, mode='w')

[parse] url: https://www.tripadvisor.com/Hotel_Review-g60713-d80999-Reviews-Grand_Hyatt_San_Francisco-San_Francisco_California.html?filterLang=en
[parse] num_reviews ALL: 5442
[parse] url_template: https://www.tripadvisor.com/Hotel_Review-g60713-d80999-Reviews-Grand_Hyatt_San_Francisco-San_Francisco_California-or{}.html?filterLang=en
[parse_reviews] url: https://www.tripadvisor.com/Hotel_Review-g60713-d80999-Reviews-Grand_Hyatt_San_Francisco-San_Francisco_California-or0.html?filterLang=en
[get_reviews_ids] data-reviewid: ['634742196', '618287952', '634488220', '634212371', '633664767']

--- review ---

  review_body : Our weekend at the Hyatt to celebrate our wedding anniversary was filled with surprises. The hotel upgraded our room, gave us a pass to the VIP Lounge and a couple of complimentary drinks to mark our special occasion. The staff was friendly, knowledgeable, professional, courteous and gracious. Couldn't ask for a better way to make this an anniversary to remember.
  review

[get_reviews_ids] data-reviewid: ['631921245', '631808974', '631518196', '631475448', '631406487']

--- review ---

  review_body : We had a Bay view from our Room and that definitely was the highlight of our stay. The room was listed at 312 sq. ft., however it did not seem that large. We had the Sunday Brunch and were terribly disappointed. The price was $34.95 per person but the quality and variety of the food was very disappointing, we do not recommend eating at the hotel. 
  review_date : November 8, 2018
  rating : <span class="ui_bubble_rating bubble_30"></span>

--- review ---

  review_body : Great location and very nice hotel for SF weekend. Friendly staff and clean hotel. Some other hotels had union strikers in front banging out catchy tunes beating on 5 gallon water jugs. Glad we were not affected at the Hyatt. The Grand Club option was very nice and would definitely do that again on my next visit. 
  review_date : November 7, 2018
  rating : <span class="ui_bubble_rating bu


  review_body : Very comfortable hotel room with great location on Union Square. NEar major shopping, Powel Street cable car line, China town, restaurants. A great location for touring. Service was very good. Refrigerator ,coffee maker in room. VA let parking with also an option to self park in garage across street.
  review_date : October 28, 2018
  rating : <span class="ui_bubble_rating bubble_40"></span>

--- review ---

  review_body : I stayed at the Hyatt for work. The experience couldn’t have been worse. First I was charged a more expensive room to accommodate for my check in. Second I was given a room on the 29th floor that was dated (from all the refurbished rooms). Third there was never complimentary water on a 350 usd a night plus tax hotel stay. Fourth breakfast was not included. Fifth the room cleanliness was non existent, towels smelled like humidity and sheets smelled like unwashed. Sixth the key never worked so I had to go back down every day to have it fixed. Seventh 

[get_reviews_ids] data-reviewid: ['623874346', '623851769', '623618542', '623615112', '623593334']

--- review ---

  review_body : One of the best experience we had at this hotelStaff, customer service, location, rooms everything was perfect will definitely use this hotel if we every cisit san francisco highly recommend this to everyone
  review_date : October 10, 2018
  rating : <span class="ui_bubble_rating bubble_50"></span>

--- review ---

  review_body : I have stayed here many times in the past 12 months. While currently undergoing lobby renovation, you would not know it. It is quiet, clean friendly. I highly recommend this hotel for its great central location. 
  review_date : October 10, 2018
  rating : <span class="ui_bubble_rating bubble_50"></span>

--- review ---

  review_body : The Grand Hyatt San Francisco is in the perfect location in Union Square. Stayed there for 5 days on business trip, staff in various departments was amazing, very attentive and polite. The Rooms 

[get_reviews_ids] data-reviewid: ['621772205', '621683434', '621670622', '621598305', '621567545']

--- review ---

  review_body : let's talk about waht was wrong, the door to the bathroom could be completely closed.the light at the foot bed is not working.And it is so noisy from the street and clim....I think it is not at the level of the price
  review_date : October 3, 2018
  rating : <span class="ui_bubble_rating bubble_30"></span>

--- review ---

  review_body : The Hotel is very central to all places of interest. The Concierge Staff is extremely polite and knowledgeable. I was disappointed by the size of the rooms and the weird sliding bathroom door made of glass, with no lock. Disturbing for co-occupants at night.
  review_date : October 2, 2018
  rating : <span class="ui_bubble_rating bubble_40"></span>

--- review ---

  review_body : My girlfriend and I loved this hotel. The bed was the best we'd slept in for a long time. Huge and comfortable. The staff were onhand and alwa

...

[get_reviews_ids] data-reviewid: ['2493456', '2492769', '2491456', '2481265', '2453458']

--- review ---

  review_body : Stayed here for about a week in August. Booked through Priceline, so the front desk didn't give us a very high floor, and put us in a ADA room (besides the grab bars in the tub, it wasn't so bad). We had a decent view of Union Square and a sliding door leading out to a hazardous balcony. Room was fine but could have used a little more warmth and furniture (the ADA rooms are a bit bigger and emptier). There is a lounge and restaurant on the top floor with great 360 views of the city. The hotel is very conveniently located, with good bus service and close to the Powell St. BART and MUNI stop. But the surrounding neighborhood isn't much fun at night and food is limited, although Chinatown is a 10 minute walk.
  review_date : August 24, 2004
  rating : <span class="ui_bubble_rating bubble_40"></span>

--- review ---

  review_body : We stayed at the Grand Hyatt a few we

[get_reviews_ids] data-reviewid: ['2447675', '2379156', '2379103', '2350077', '2333105']

--- review ---

  review_body : We stayed 5 nights at this hotel. We got a great rate through priceline. Because we had a reduced rate, we were OK with the extra charges... like $10 a day for internet access and expensive valet parking. Overall we found the staff to be friendly and the 2 occasions we used valet parking the car was waiting for us when we got to there. Like previous reviewers we found the system that automatically recorded purchases from the mini bar odd, and based on previous reviews we discarded our wine bottle out side of the hotel to avoid the 'corkage fee'. Our room was a bit small, but was comfortable for two people. Also the window to our balcony opened, and we were able to step outside onto it - which was a little scary even on the 10th floor. The view was great from our room, we could see from one side of the bay to the other. Our room was also quiet. The location was great

[get_reviews_ids] data-reviewid: ['2152510', '2142948', '2131798', '2071019', '1834844']

--- review ---

  review_body : My husband and I just returned from a 6 night stay at the Grand Hyatt, and it was wonderful. It was our first visit to San Francisco, and we were celebrating our 3rd anniversary, so I asked for a higher-level floor room with king sized bed upon check-in, and they gave us a great room on the 23rd floor, with a view of the city and the water, for guestroom rates! Once in the room, totally exhausted from taking a 7 a.m. flight from NY, needing a nap desperately, I phoned housekeeping to ask if they had a pair of slippers, as I had forgotten mine. Within 10 minutes they brought me a new pair of slippers! Room was very clean and lots of towels in the bathroom. The concierge desk was also fabulous - we left our Pac Bell game tickets home, so they directed us to the business office where we were able to go online to get a customer service number for the park, call them, an

[get_reviews_ids] data-reviewid: ['1532905', '1420240', '1399092', '1375673', '1372149']

--- review ---

  review_body : I used the reviews from this website and booked a rather expensive Regency Club room. What a mistake. Dated 2 star hotel trying to be a 4 star. The location is great, but on the 30th floor, I could easily hear the street traffic due to a lack of modern glazed window glass. Add on the noise I could hear from rooms above, and I could say it was one of the biggest hotel disappoinments I have had. After not sleeping, I called the Four Seasons and got a room in there at 9:00 AM. What a hotel. With their Holiday rate it was $80/night more than the Hyatt, but absolutely incompararable. I felt like I moved from a 30 some odd story buget hotel to the Taj Mahal.
  review_date : December 29, 2003
  rating : <span class="ui_bubble_rating bubble_20"></span>

--- review ---

  review_body : The grand Hyatt is my sure stay every time in San Francisco, good service, big room, good 

[get_reviews_ids] data-reviewid: ['1042836', '853453']

--- review ---

  review_body : We spent our anniversery at the Grand Hyatt and had a wonderfull stay. Check in was fast, friendly and efficient, we used our Free nights Faster credits for 4 free nights, and because it was our anniversery we were upgraded to the Club level. The view form the 31st floor was amazing, the lounge was beautiful, breakfast and evening snacks were very good, and the room comfortable. We found the bed very good, the room was made up early, bus stops for everywhere we wanted to go was handy. The only bad note was the speed of the elevators, they were very slow, and the doors closed very fast, you had to rush to get in. If you bring a car parking is also very expensive, we took the bus, cable car or street car were ever we went, with the pass very inexpensive and much easier.
  review_date : June 3, 2003
  rating : <span class="ui_bubble_rating bubble_50"></span>

--- review ---

  review_body : Having trav

In [19]:
import pandas as pd
import numpy as np
import re

In [20]:
hotel = pd.read_csv('Grand_Hyatt_San_Francisco-San_Francisco_California__en.csv')

In [21]:
hotel

review_body         review_date  \
0     Our weekend at the Hyatt to celebrate our wedd...   November 20, 2018   
1     We stayed here 4 nights the standards met were...  September 20, 2018   
2     The Hyatt is very central and convenient to wa...   November 19, 2018   
3     This hotel is in a great location. The hotel r...   November 18, 2018   
4     The location doesn't get much better than wher...   November 15, 2018   
5     Dirty hallways, loud rooms, terrible restauran...   November 15, 2018   
6     Right by Union Square, can walk everywhere or ...   November 13, 2018   
7     Brand you can trust to deliver a superior expe...   November 13, 2018   
8     We stayed in room 2124, an executive suite. Th...   November 13, 2018   
9     Typical Hyatt and nothing wrong with it. We go...   November 13, 2018   
10    The location is great, I stayed here for a con...   November 11, 2018   
11    Booked here with work and I know I can expect ...    November 9, 2018   
12    Room was very clean and people very kind, we d...    November 9, 2018   
13    we stayed a total of 6 nights over two periods...    November 8, 2018   
14    Staff was very professional! Concierge service...    November 8, 2018   
15    We had a Bay view from our Room and that defin...    November 8, 2018   
16    Great location and very nice hotel for SF week...    November 7, 2018   
17    We have stayed here three other times and pref...    November 6, 2018   
18    I had stayed at many Hyatt hotels in the US & ...    November 6, 2018   
19    No customer appreciation! We stay here several...    November 6, 2018   
20    Very poor sound isolation between rooms, espec...    November 3, 2018   
21    Fabulous fabulous fabulous as always and a rea...    November 3, 2018   
22    Was pleasantly surprised at how great this hot...    October 30, 2018   
23    Fine hotel and great location. Grand Club was ...    October 30, 2018   
24    Stayed on 27th floor great city view. Classy p...    October 30, 2018   
25    Nice location close to CVS, Starbucks, Apple S...    October 29, 2018   
26    Large rooms, with lots of nice touches. I like...    October 29, 2018   
27    Great location-smack in the middle of Union Sq...    October 28, 2018   
28    Very comfortable hotel room with great locatio...    October 28, 2018   
29    I stayed at the Hyatt for work. The experience...    October 25, 2018   
...                                                 ...                 ...   
4622  This is a very exciting hotel to stay at. It i...        July 3, 2004   
4623  This is a great business hotel! I have stayed ...       June 12, 2004   
4624  I've stayed in a number of the 4**** hotels in...        June 7, 2004   
4625  My husband and I just returned from a 6 night ...        June 3, 2004   
4626  I am normally always impressed with Hyatt. Thi...        May 31, 2004   
4627  I stayed 5 nights at the Grand Hyatt SF in Apr...        May 30, 2004   
4628  Just came back from one night at the Grand Hya...        May 16, 2004   
4629  We stayed at this hotel the first week in Apri...      April 23, 2004   
4630  Just returned from San Francisco trip. San Fra...      March 22, 2004   
4631  Stayed at the Hyatt over Valentine's Day weeke...      March 17, 2004   
4632  Booked trip through Travelocity, initially on ...   February 29, 2004   
4633  The Grand Hyatt at Union Square is a good loca...   February 17, 2004   
4634  Stayed at the Grand Hyatt through a Hotwire ra...    January 19, 2004   
4635  I used the reviews from this website and booke...   December 29, 2003   
4636  The grand Hyatt is my sure stay every time in ...    October 22, 2003   
4637  Stayed at the Grand Hyatt for 2 nights @ $199/...    October 18, 2003   
4638  We stayed here for 3 nights. Ideally located i...     October 3, 2003   
4639  This a great hotel and the service was excella...  September 29, 2003   
4640  My 8/28 - 9/1 stay at the Grand Hyatt was just...   September 3, 2003   
4641  Excellent

In [22]:
hotel = pd.read_csv('Grand_Hyatt_San_Francisco-San_Francisco_California__en.csv')
i = 0
rating = []
while i < len(hotel):
    extract  = float(re.findall(r'\d{2}', hotel.iloc[i]['rating'])[0])
    rating.append(extract/10)
    i+=1
hotel['rating'] = rating

In [23]:
hotel.to_csv(r'/Users/a1/Desktop/MBA study/Courses/Marketing Analytics Projects/Text Mining/Grand_Hyatt.csv', index = None, header=True)